In [1]:
# Notebook parameters. Values here are for development only and 
# will be overridden when running via snakemake and papermill.
cohort_id = "CD-NU_Gbadolite_gamb_2015_Q3"
# cohort_id = 'ML-2_Kati_colu_2014_Q3'
# cohort_id = 'CI-LG_Agneby-Tiassa_colu_2012'
cohorts_analysis = "20230223"
contigs = ['2RL', '3RL', 'X']
sample_sets = "3.0"
min_cohort_size = 20
max_cohort_size = 50
h12_calibration_contig = '3L'
use_gcs_cache = False
dask_scheduler = "threads"

In [2]:
# Parameters
min_cohort_size = 20
max_cohort_size = 50
sample_sets = ["3.0"]
contigs = ["2RL", "3RL", "X"]
cohorts_analysis = "20230223"
h12_calibration_contig = "3L"
h12_signal_detection_min_delta_aic = 1000
h12_signal_detection_min_stat_max = 0.1
h12_signal_detection_gflanks = [6]
use_gcs_cache = False
dask_scheduler = "single-threaded"
cohort_id = "GN-N_Macenta_gamb_2012_Q4"


In [3]:
from IPython.display import Markdown, HTML
import malariagen_data
import numpy as np
import pandas as pd
from pyprojroot import here
import yaml
import dask
dask.config.set(scheduler=dask_scheduler);
from textwrap import dedent

import geopandas as gpd
import bokeh.layouts as bklay
import bokeh.plotting as bkplt
import bokeh.models as bkmod
import plotly.express as px

from bokeh.io import output_notebook # enables plot interface in J notebook

# N.B., do not add the "remove-output" tag to this cell!!! If you do,
# the bokeh javascript libraries will not get loaded in the generated
# HTML page. The call to output_notebook() injects javascript in the
# cell output which triggers the bokeh javascript libraries to be loaded
# in the page.
output_notebook(hide_banner=True)

# Guinea / Macenta / gambiae / 2012 / Q4

In [4]:
# Load cohorts to find sample query to select samples for this cohort.

df_cohorts = gpd.read_file(here() / "build" / "final_cohorts.geojson").set_index("cohort_id")
cohort = df_cohorts.loc[cohort_id]
cohort

cohort_size                                                          51
country                                                          Guinea
admin1_iso                                                         GN-N
admin1_name                                                   Nzerekore
admin2_name                                                     Macenta
taxon                                                           gambiae
year                                                               2012
quarter                                                               4
cohort_label                     Guinea / Macenta / gambiae / 2012 / Q4
sample_query          cohort_admin2_quarter == 'GN-N_Macenta_gamb_20...
latitude                                                           8.48
longitude                                                         -9.53
h12_window_size                                                  1000.0
country_alpha2                                                  

In [5]:
# Initialise access to MalariaGEN data.

extra_params = dict()
if use_gcs_cache:
    extra_params["url"] = "simplecache::gs://vo_agam_release"
    extra_params["simplecache"] = dict(cache_storage=(here() / "gcs_cache").as_posix())

ag3 = malariagen_data.Ag3(
    # Pin the version of the cohorts analysis for reproducibility.
    cohorts_analysis=cohorts_analysis,
    results_cache=(here() / "malariagen_data_cache").as_posix(),
    **extra_params,
)
ag3

<MalariaGEN Ag3 API client>
Storage URL             : gs://vo_agam_release/
Data releases available : 3.0, 3.1, 3.2, 3.3, 3.4, 3.5, 3.6, 3.7, 3.8
Results cache           : /home/sanjaynagi/selection-atlas/malariagen_data_cache
Cohorts analysis        : 20230223
AIM analysis            : 20220528
Site filters analysis   : dt_20200416
Software version        : malariagen_data 7.13.0
Client location         : unknown
---
Please note that data are subject to terms of use,
for more information see https://www.malariagen.net/data
or contact data@malariagen.net. For API documentation see 
https://malariagen.github.io/vector-data/ag3/api.html

In [6]:
# Load sample metadata for this cohort.

df_samples = ag3.sample_metadata(sample_query=cohort['sample_query'])
df_samples

sample_id partner_sample_id  contributor country  location  year  month  \
0    AV0043-C             KD306  Ken Vernick  Guinea  Koundara  2012     10   
1    AV0036-C             KD170  Ken Vernick  Guinea  Koundara  2012     10   
2    AV0037-C             KD177  Ken Vernick  Guinea  Koundara  2012     10   
3    AV0026-C             KD005  Ken Vernick  Guinea  Koundara  2012     10   
4    AV0032-C             KD130  Ken Vernick  Guinea  Koundara  2012     10   
5    AV0035-C             KD159  Ken Vernick  Guinea  Koundara  2012     10   
6    AV0031-C             KD105  Ken Vernick  Guinea  Koundara  2012     10   
7    AV0027-C             KD029  Ken Vernick  Guinea  Koundara  2012     10   
8    AV0047-C             KD363  Ken Vernick  Guinea  Koundara  2012     10   
9    AV0039-C             KD248  Ken Vernick  Guinea  Koundara  2012     10   
10   AV0041-C             KD264  Ken Vernick  Guinea  Koundara  2012     10   
11   AV0033-C             KD148  Ken Vernick  Guinea  Koundara  2012     10   
12   AV0045-C             KD339  Ken Vernick  Guinea  Koundara  2012     10   
13   AV0028-C             KD034  Ken Vernick  Guinea  Koundara  2012     10   
14  AV0044-Cx             KD309  Ken Vernick  Guinea  Koundara  2012     10   
15  AV0030-Cx             KD104  Ken Vernick  Guinea  Koundara  2012     10   
16  AV0029-Cx             KD044  Ken Vernick  Guinea  Koundara  2012     10   
17  AV0034-Cx             KD156  Ken Vernick  Guinea  Koundara  2012     10   
18  AV0235-CW            KV0890  Ken Vernick  Guinea  Koundara  2012     10   
19   AV0142-C            KV0630  Ken Vernick  Guinea  Koundara  2012     10   
20   AV0154-C            KV0631  Ken Vernick  Guinea  Koundara  2012     10   
21   AV0226-C            KV0638  Ken Vernick  Guinea  Koundara  2012     10   
22   AV0143-C            KV0639  Ken Vernick  Guinea  Koundara  2012     10   
23   AV0179-C            KV0642  Ken Vernick  Guinea  Koundara  2012     10   
24   AV0191-C            KV0644  Ken Vernick  Guinea  Koundara  2012     10   
25   AV0180-C            KV0653  Ken Vernick  Guinea  Koundara  2012     10   
26   AV0192-C            KV0654  Ken Vernick  Guinea  Koundara  2012     10   
27   AV0170-C            KV0675  Ken Vernick  Guinea  Koundara  2012     10   
28   AV0194-C            KV0677  Ken Vernick  Guinea  Koundara  2012     10   
29   AV0206-C            KV0691  Ken Vernick  Guinea  Koundara  2012     10   
30   AV0218-C            KV0694  Ken Vernick  Guinea  Koundara  2012     10   
31   AV0171-C            KV0717  Ken Vernick  Guinea  Koundara  2012     10   
32   AV0195-C            KV0723  Ken Vernick  Guinea  Koundara  2012     10   
33   AV0219-C            KV0728  Ken Vernick  Guinea  Koundara  2012     10   
34   AV0231-C            KV0730  Ken Vernick  Guinea  Koundara  2012     10   
35   AV0160-C            KV0739  Ken Vernick  Guinea  Koundara  2012     10   
36   AV0196-C            KV0746  Ken Vernick  Guinea  Koundara  2012     10   
37   AV0208-C            KV0748  Ken Vernick  Guinea  Koundara  2012     10   
38   AV0185-C            KV0765  Ken Vernick  Guinea  Koundara  2012     10   
39   AV0162-C            KV0872  Ken Vernick  Guinea  Koundara  2012     10   
40   AV0186-C            KV0874  Ken Vernick  Guinea  Koundara  2012     10   
41   AV0198-C            KV0876  Ken Vernick  Guinea  Koundara  2012     10   
42   AV0210-C            KV0877  Ken Vernick  Guinea  Koundara  2012     10   
43   AV0199-C            KV0886  Ken Vernick  Guinea  Koundara  2012     10   
44   AV0164-C            KV0895  Ken Vernick  Guinea  Koundara  2012     10   
45   AV0188-C            KV0897  Ken Vernick  Guinea  Koundara  2012     10   
46   AV0200-C            KV0899  Ken Vernick  Guinea  Koundara  2012     10   
47   AV0177-C            KV0906  Ken Vernick  Guinea  Koundara  2012     10   
48   AV0189-C            KV0907  Ken Vernick  Guinea  Koundara  2012     10   
49   AV0201-C            KV0909  Ken Vernick  Guinea  

In [7]:
# Determine collection dates.

df_collection_dates = (
    df_samples
    .groupby(["year", "month"])
    .size()
    .reset_index()
    .rename(columns={0: 'count'})
)
df_collection_dates

year  month  count
0  2012     10     51

In [8]:
# Determine first and last collection months.

min_month = df_collection_dates["month"].min()
max_month = df_collection_dates["month"].max()

if min_month < 0:
    start_month = end_month = None
else:
    start_month = pd.to_datetime(min_month, format="%m").month_name()
    end_month = pd.to_datetime(max_month, format="%m").month_name()
    
start_month, end_month

('October', 'October')

In [9]:
# Determine unique collection locations.

df_locations = df_samples[["location", "longitude", "latitude"]].drop_duplicates()
df_locations

location  longitude  latitude
0  Koundara      -9.53      8.48

In [10]:
# Extract provenance information about the samples.

df_contributors = df_samples[["release", "sample_set", "contributor"]].drop_duplicates()
df_contributors["study"] = df_contributors.apply(
    lambda v: "Ag1000G" if v["sample_set"].startswith("AG1000G") else "TODO",
    axis="columns"
)
df_contributors["release"] = df_contributors["release"].apply(
    lambda v: f"Ag{v}"
)
df_contributors.rename(columns={
    "contributor": "Contributor",
    "study": "Study",
    "release": "Data release",
    "sample_set": "Sample set",
}, inplace=True)
df_contributors.set_index(["Contributor", "Study", "Data release"], inplace=True)
df_contributors

Sample set
Contributor Study   Data release              
Ken Vernick Ag1000G Ag3.0         AG1000G-GN-A
                    Ag3.0         AG1000G-GN-B

In [11]:
# Build a paragraph with summary information about the samples in this cohort.

n_locations = len(df_locations)

summary_info = f"""This cohort comprises {cohort['cohort_size']:,} samples from the 
*{cohort['taxon']}* taxon, collected from {n_locations} locations within the administrative 
division of {cohort['admin2_name']}, {cohort['admin1_name']}, {cohort['country']}."""

if start_month and start_month == end_month:
    summary_info += f""" Collections were made in {start_month} {cohort['year']}."""
elif start_month:
    summary_info += f""" Collections were made between {start_month} and {end_month} in {cohort['year']}."""
else:
    summary_info += f""" Collections were made in {cohort['year']}."""
    
display(Markdown(summary_info))


This cohort comprises 51 samples from the 
*gambiae* taxon, collected from 1 locations within the administrative 
division of Macenta, Nzerekore, Guinea. Collections were made in October 2012.

## Selection scans

In [12]:
# load signals to overlay on H12 plots
import pandas as pd

df_signals_contigs = []
for contig in contigs:

    try:
        df_signals_contig = pd.read_csv(here() / "build/h12-signal-detection/" / f"{cohort_id}_{contig}.csv")
    except pd.errors.EmptyDataError:
        df_signals_contig = pd.DataFrame()
    df_signals_contigs.append(df_signals_contig)  
    
df_signals = pd.concat(df_signals_contigs)

# Add extra columns to help with overlaying signals on plots.
df_signals["bottom"] = 0
df_signals["top"] = 1

df_signals

cohort_id contig     gcenter    pcenter  delta_i  stat_max  \
0  GN-N_Macenta_gamb_2012_Q4    2RL   56.922576   28461288     7498    0.3576   
1  GN-N_Macenta_gamb_2012_Q4    2RL  120.656309   64098786     3179    0.9606   
2  GN-N_Macenta_gamb_2012_Q4    2RL  172.694787   90118025     3435    0.3310   
3  GN-N_Macenta_gamb_2012_Q4    2RL  194.150423  100845843     2997    0.1466   
0  GN-N_Macenta_gamb_2012_Q4    3RL   56.999488   28499744     5353    0.3526   
0  GN-N_Macenta_gamb_2012_Q4      X   30.498264   15249132     3010    0.3768   

     gpos_max   ppos_max  focus_gstart  focus_gstop  ...      skew  \
0   56.942336   28471168     56.839266    57.061325  ... -0.367957   
1  120.596352   64068807    120.329098   120.953242  ...  0.070041   
2  172.414576   89977919    172.356698   172.863831  ...  0.500000   
3  194.098898  100820080    194.115070   194.168115  ...  0.499377   
0   57.119268   28559634     56.917568    57.096217  ... -0.119868   
0   30.416788   15208394     30.340123    30.621430  ...  0.180301   

   decay_left  decay_right  baseline           aic           bic        rss  \
0    0.333240     0.554996  0.017088 -19304.739130 -19276.598974   0.170185   
1    1.308843     1.187732  0.039508  -7148.721780  -7122.066478  14.054812   
2    1.352355     0.676177  0.034084 -13043.071724 -13015.400582   1.746663   
3    0.141412     0.070767  0.017439 -20841.927335 -20814.106143   0.038732   
0    0.327678     0.386915  0.023025 -16180.240500 -16152.542706   0.343801   
0    0.632561     0.492664  0.028130 -14555.561992 -14527.751184   0.991738   

   constant_aic  bottom  top  
0 -11806.062855       0    1  
1  -3969.470927       0    1  
2  -9607.603664       0    1  
3 -17844.316612       0    1  
0 -10826.270126       0    1  
0 -11545.096779       0    1  

[6 rows x 32 columns]

In [13]:
# load window sizes 
h12_calibration_dir = "build/h12-calibration"
with open(here() / h12_calibration_dir / f"{cohort_id}.yaml") as h12_calibration_file:
    h12_calibration_params = yaml.safe_load(h12_calibration_file)
h12_window_size = h12_calibration_params["h12_window_size"]
g123_calibration_dir = "build/g123-calibration"
with open(here() / g123_calibration_dir / f"{cohort_id}.yaml") as g123_calibration_file:
    g123_calibration_params = yaml.safe_load(g123_calibration_file)
g123_window_size = g123_calibration_params["g123_window_size"]

if cohort.taxon == 'arabiensis':
    phasing_analysis = 'arab'
else:
    phasing_analysis = 'gamb_colu'

ihs_window_size = 100

def plot_h12_g123_ihs_tracks(
        contig, 
        df_signals,
        sizing_mode='stretch_width', 
        show=False, 
        width=800, 
        track_height=150,
        genes_height=90,
    ):

    sample_query = cohort["sample_query"]
    
    fig1 = ag3.plot_h12_gwss_track(
        contig=contig, 
        window_size=h12_window_size, 
        analysis=phasing_analysis, 
        sample_sets=sample_sets,
        sample_query=sample_query, 
        min_cohort_size=min_cohort_size,
        max_cohort_size=max_cohort_size,
        sizing_mode=sizing_mode,
        show=show,
        width=width,
        height=track_height,
    )
    fig1.xaxis.visible = False
        
    if not df_signals.empty:
        df = df_signals.query("contig == @contig")
        center_xs = [np.array([row.pcenter, row.pcenter]) for idx, row in df.iterrows()]
        center_ys = [np.array([0, 1]) for idx, row in df.iterrows()]
        source = bkmod.ColumnDataSource(data={
            'cohort': df.cohort_id,
            'chromosome': df.contig,
            'score': df.delta_i.astype(int),
            'peak_start': df.span2_pstart,
            'peak_stop': df.span2_pstop,
            'focus_start': df.focus_pstart,
            'focus_stop': df.focus_pstop,    
            'center_xs': center_xs,
            'center_ys': center_ys,
            'bottom': df.bottom ,
            'top': df.top,
            })
        quad = fig1.quad(bottom='bottom', top='top', left='peak_start', right='peak_stop', 
              source=source, color="gray", alpha=.1, line_width=1)
        quad2 = fig1.quad(bottom='bottom', top='top', left='focus_start', right='focus_stop', 
              source=source, color="red", alpha=.4)
        glyph = bkmod.MultiLine(xs='center_xs', ys='center_ys', line_color='red', line_width=2, line_alpha=0.8)
        fig1.add_glyph(source, glyph)
    
        hover = bkmod.HoverTool(tooltips=[
            ("Cohort", '@cohort'),
            ("Score", '@score'),
            ("Focus", "@focus_start{,} - @focus_stop{,}"),
        ], renderers=[quad])

        fig1.add_tools(hover)
    
    fig2 = ag3.plot_g123_gwss_track(
        contig=contig, 
        window_size=g123_window_size, 
        sites=phasing_analysis,
        site_mask=phasing_analysis, 
        sample_sets=sample_sets,
        sample_query=sample_query, 
        min_cohort_size=min_cohort_size,
        max_cohort_size=max_cohort_size,
        sizing_mode=sizing_mode,
        width=width,
        height=track_height,
        show=show,
        title="",
        x_range=fig1.x_range,
    )
    fig2.xaxis.visible = False

    fig3 = ag3.plot_ihs_gwss_track(
        contig=contig, 
        window_size=ihs_window_size, 
        analysis=phasing_analysis, 
        sample_sets=sample_sets,
        sample_query=sample_query, 
        min_cohort_size=min_cohort_size,
        max_cohort_size=max_cohort_size,
        sizing_mode=sizing_mode,
        width=width,
        height=track_height,
        show=show,
        title="",
        x_range=fig1.x_range,
    )
    fig3.xaxis.visible = False


    fig4 = ag3.plot_genes(
        region=contig, 
        show=show,
        sizing_mode=sizing_mode,
        width=width,
        height=genes_height,
        x_range=fig1.x_range
        )
                        
    fig = bklay.gridplot(
        [fig1, fig2, fig3, fig4],
        ncols=1,
        toolbar_location="above",
        merge_tools=True,
        sizing_mode=sizing_mode,
    )
    return fig 

In [14]:
for contig in contigs:
    
    display(HTML(f"<h3>Chromosome {contig}</h3>"))
    
    fig = plot_h12_g123_ihs_tracks(
        contig=contig,
        df_signals=df_signals,
    );

    bkplt.show(fig)


## Sampling information

In [15]:
from ipyleaflet import Map, Marker, basemaps
from ipywidgets import HTML

center = cohort[['latitude', 'longitude']].to_list()
m = Map(center=center, zoom=9, basemap=basemaps.OpenTopoMap)

df = df_samples[['latitude', 'longitude', 'taxon']].groupby(['latitude', 'longitude', 'taxon']).size().to_frame().rename(columns={0: 'count'}).reset_index()

for coh_id, row in df.iterrows():
    lat, long = row[['latitude', 'longitude']]
    
    if row['taxon'] == 'gambiae':
        color= 'red'
    elif row['taxon'] == 'coluzzii':
        color='cadetblue'
    elif row['taxon'] == 'arabiensis':
        color='lightgreen'
    else: 
        color='gray'

    marker = Marker(location=(lat, long), draggable=True, opacity=0.7, color=color)
    m.add_layer(marker);

    message2 = HTML()
    message2.value = f"n = {row['count']}"
    marker.popup = message2

display(m)

Map(center=[8.48, -9.53], controls=(ZoomControl(options=['position', 'zoom_in_text', 'zoom_in_title', 'zoom_ou…

In [16]:

if min_month >= 0:
    # For this cohort we have month data, so show a breakdown of sample
    # numbers by location and month.
    
    # Construct a pivot table counting samples.
    df_loc_dt = df_samples.pivot_table(
        index=["location", "longitude", "latitude"],
        columns="month",
        values="sample_id",
        aggfunc="count",
        fill_value=0,
    )

    # Tidy up the columns using a multi index.
    df_loc_dt.reset_index(inplace=True)
    cols = pd.MultiIndex.from_tuples(
        [("Location", "Name"), ("Location", "Longitude"), ("Location", "Latitude")] + 
        [("Date", pd.to_datetime(x, format="%m").month_name()) 
         for x in df_loc_dt.columns[3:]], 
    )
    df_loc_dt.columns = cols
    
else:
    # For this cohort we do not have month data, so show a breakdown of sample
    # numbers by location only.
    
    # Construct a pivot table counting samples.
    df_loc_dt = df_samples.groupby(["location", "longitude", "latitude"]).agg({"sample_id": "count"})

    # Tidy up the columns using a multi index.
    df_loc_dt.reset_index(inplace=True)
    cols = pd.MultiIndex.from_tuples(
        [("Location", "Name"), ("Location", "Longitude"), ("Location", "Latitude"), ("Date", cohort.year)]
    )
    df_loc_dt.columns = cols

# Style the table.
df_loc_dt_styled = (
    df_loc_dt
    .style
    .format(precision=3)
    .set_caption("Number of samples collected.")
    .hide()
)
display(df_loc_dt_styled)    

## Diagnostics
### H12 calibration

In [17]:
display(Markdown(f"Selected window size: **{h12_window_size:,}**"))

window_sizes = (100, 200, 500, 1000, 2000, 5000, 10000, 20000)

ag3.plot_h12_calibration(
    contig=h12_calibration_contig,
    analysis=phasing_analysis,
    sample_sets=sample_sets,
    sample_query=cohort['sample_query'],
    min_cohort_size=min_cohort_size,
    max_cohort_size=max_cohort_size,
    window_sizes=window_sizes,
);


Selected window size: **1,000**

### G123 Calibration

In [18]:
display(Markdown(f"Selected window size: **{g123_window_size:,}**"))

ag3.plot_g123_calibration(
    contig=h12_calibration_contig,
    sites=phasing_analysis,
    site_mask=phasing_analysis,
    sample_sets=sample_sets,
    sample_query=cohort['sample_query'],
    min_cohort_size=min_cohort_size,
    max_cohort_size=max_cohort_size,
    window_sizes=window_sizes,
);

Selected window size: **500**

## Data sources

In [19]:
df_sources_style = (
    df_contributors
    .style
    .set_caption("MalariaGEN Vector Observatory partners, studies and sample sets contributing data for this cohort.")
)
df_sources_style